In [1]:
# file: brazil_regions_heatmap.py

import folium
import json
import pandas as pd
import requests
from branca.colormap import linear

# Porcentagens por região personalizada
region_data = {
    "Norte": 17.4,
    "Nordeste - norte": 15.0,
    "Nordeste - sul": 18.1,
    "São paulo": 23.0,
    "Sudeste": 20.5,
    "Sul": 23.3
}

# Mapeamento de estados para regiões personalizadas
region_mapping = {
    # Norte
    "AC": "Norte", "AP": "Norte", "AM": "Norte", "PA": "Norte", "RO": "Norte", "RR": "Norte", "TO": "Norte",

    # Nordeste - norte
    "MA": "Nordeste - norte", "PI": "Nordeste - norte", "CE": "Nordeste - norte",
    "RN": "Nordeste - norte", "PB": "Nordeste - norte", "PE": "Nordeste - norte",

    # Nordeste - sul
    "AL": "Nordeste - sul", "SE": "Nordeste - sul", "BA": "Nordeste - sul",

    # Sudeste (sem SP)
    "MG": "Sudeste", "RJ": "Sudeste", "ES": "Sudeste",

    # São Paulo
    "SP": "São paulo",

    # Sul
    "PR": "Sul", "SC": "Sul", "RS": "Sul"
}

# Baixar GeoJSON dos estados brasileiros
geojson_url = 'https://raw.githubusercontent.com/codeforamerica/click_that_hood/master/public/data/brazil-states.geojson'
geojson_data = requests.get(geojson_url).json()

# Construir DataFrame de estado -> porcentagem
state_data = []
centroids = {}
region_centroid = {}
region_states = {}

for feature in geojson_data['features']:
    state_abbr = feature['properties']['sigla']
    region = region_mapping.get(state_abbr)
    percent = region_data.get(region)
    coords = feature['geometry']['coordinates'][0]

    # calcular centro aproximado (média dos pontos)
    if feature['geometry']['type'] == 'Polygon':
        lon = sum([point[0] for point in coords]) / len(coords)
        lat = sum([point[1] for point in coords]) / len(coords)
    elif feature['geometry']['type'] == 'MultiPolygon':
        coords = feature['geometry']['coordinates'][0][0]
        lon = sum([point[0] for point in coords]) / len(coords)
        lat = sum([point[1] for point in coords]) / len(coords)
    else:
        lon, lat = 0, 0

    centroids[state_abbr] = (lat, lon)
    state_data.append({"state": state_abbr, "region": region, "percent": percent})

    if region not in region_centroid:
        region_centroid[region] = []
    region_centroid[region].append((lat, lon))

    if region not in region_states:
        region_states[region] = set()
    region_states[region].add(state_abbr)

df = pd.DataFrame(state_data)

# Criar colormap azul (claro até escuro)
colormap = linear.Blues_09.scale(df["percent"].min(), df["percent"].max())
colormap.caption = "Porcentagem de Ruptura Bruta por região"

# Criar mapa centrado apenas no Brasil com fundo branco (usar "white tile")
white_tile_url = "https://tiles.wmflabs.org/bw-mapnik/{z}/{x}/{y}.png"
m = folium.Map(location=[-14.2350, -51.9253], zoom_start=4, tiles=white_tile_url, attr='Wikimedia')

# Adicionar o choropleth com estados não preenchidos em cinza claro
folium.Choropleth(
    geo_data=geojson_data,
    name="choropleth",
    data=df,
    columns=["state", "percent"],
    key_on="feature.properties.sigla",
    fill_color="Blues",
    fill_opacity=0.9,
    line_opacity=0.5,
    line_color="black",
    nan_fill_color="#dddddd",
    nan_fill_opacity=1,
    highlight=True,
    legend_name="Porcentagem de Ruptura Bruta por região"
).add_to(m)

# Adicionar uma única label por região (fonte maior)
for region, coords in region_centroid.items():
    if region and region in region_data:
        lat = sum([c[0] for c in coords]) / len(coords)
        lon = sum([c[1] for c in coords]) / len(coords)
        percent = region_data[region]
        folium.map.Marker(
            [lat, lon],
            icon=folium.DivIcon(html=f'<div style="font-size:16pt; color:black; text-align:center">{percent:.1f}%</div>')
        ).add_to(m)

# Adicionar colormap
colormap.add_to(m)

# Salvar o mapa
m.save("heatmap_brasil2.html")
